In [1]:
from text_decomposition_prompt import text_decomposition_prompt
print(text_decomposition_prompt("TEST"))


--Goal--
Given a text, segment it into multiple semantic units, each containing detailed descriptions of specific events or activities.
Perform the following tasks:
--Steps--
1. Provide a summary for each semantic unit while retaining all crucial details relevant to the original context.
2. Extract all entities directly from the original text of each semantic unit, not from the paraphrased. Format each entity name in UPPERCASE. You should extract all entities including times, locations, people, organizations and all kinds of entities.
3. From the entities extracted in Step 2, list all relationships within the semantic unit and the corresponding original context in the form of string separated by comma: "ENTITY_A, RELATION_TYPE, ENTITY_B". The RELATION_TYPE could be a descriptive sentence, while the entities involved in the relationship must come from the entity names extracted in Step 2. Please make sure the string contains three elements representing two entities and the relationship 

In [2]:
with open(r"C:\Users\HP\Desktop\Projects\NodeRAG\API_KEY.txt", "r", encoding="utf-8") as f:
    API_KEY = f.read()

In [3]:
import pandas as pd
novel_chunks_path = r"C:\Users\HP\Desktop\Projects\NodeRAG\chunking\novel_chunks.parquet" 

In [4]:
novel_chunks = pd.read_parquet(novel_chunks_path)
novel_chunks

chunk_id  corpus_name  \
0            0  Novel-30752   
1            1  Novel-30752   
2            2  Novel-30752   
3            3  Novel-30752   
4            4  Novel-30752   
...        ...          ...   
2624       127  Novel-44557   
2625       128  Novel-44557   
2626       129  Novel-44557   
2627       130  Novel-44557   
2628       131  Novel-44557   

                                                  chunk  chunk_length  
0     Produced by Julia Miller and the Online Distri...           397  
1     Entered according to an Act of Congress, in De...           372  
2     To-day the inhabitants of Yucatan are even ign...           379  
3     I have visited a few, certainly extremely beau...           396  
4     Many strange stories are told by the aborigine...           373  
...                                                 ...           ...  
2624  Whether the ruin on the opposite height was on...           392  
2625  No sooner had we rounded the rock, than the ba...           395  
2626  And before we knew what was happening, we foun...           388  
2627  Two more pictures remain, the last gorgeous su...           383  
2628  If Arthur could "come again"--perhaps in the p...           176  

[2629 rows x 4 columns]

In [5]:
from google import genai

def call_gemini(text):
    client = genai.Client(api_key = API_KEY)
    response = client.models.generate_content(
        model="gemini-2.5-flash-lite",
        contents=text_decomposition_prompt(text),
    )
    return response.text

In [6]:
import os
path = "novel_responses.parquet"
if os.path.exists(path):
    df = pd.read_parquet(path)
    responses = dict(zip(df["index"], df["response"]))
else:
    responses = {}

responses

{0: '```json\n[\n  {\n    "semantic_unit": "This document was produced by Julia Miller and the Online Distributed Proofreading Team, with images provided by The Internet Archive/American Libraries. The transcriber notes that typographical errors are marked with [TN-#], and inconsistent spelling, hyphenation, and capitalization have been maintained, with a list available at the end of the text. Oe ligatures have been expanded, and special characters like the Sun symbol and accented letters are represented by specific codes.",\n    "entities": [\n      "JULIA MILLER",\n      "ONLINE DISTRIBUTED PROOFREADING TEAM",\n      "HTTP://WWW.PGDP.NET",\n      "THE INTERNET ARCHIVE/AMERICAN LIBRARIES",\n      "[TN-#]",\n      "OE LIGATURES",\n      "[SUN]",\n      "[=A]",\n      "[C]",\n      "[C]"\n    ],\n    "relationships": [\n      "This document, produced by, JULIA MILLER",\n      "This document, produced by, ONLINE DISTRIBUTED PROOFREADING TEAM",\n      "JULIA MILLER, works with, ONLINE DIS

In [7]:
stop here

SyntaxError: invalid syntax (4067800170.py, line 1)

In [ ]:
from tqdm import tqdm

start_idx = 1676
end_idx = len(novel_chunks)
for idx, row in tqdm(novel_chunks.iloc[start_idx:end_idx].iterrows()):
    chunk_text = row['chunk']
    value = call_gemini(chunk_text)
    key = idx
    responses[key] = value
    if idx % 10 == 0:
        print("Key:", key)
        print('-'*40)

In [ ]:
stop here

In [8]:
from tqdm import tqdm
idx_list = sorted([267, 1989, 1876, 1648, 1616, 1384, 789, 2624])
for idx in tqdm(idx_list):
    row = novel_chunks.loc[idx]
    chunk_text = row['chunk']
    value = call_gemini(chunk_text)
    key = idx
    responses[key] = value
    print("Key:", key)

 12%|█▎        | 1/8 [00:07<00:55,  7.96s/it]

Key: 267


 25%|██▌       | 2/8 [00:31<01:42, 17.09s/it]

Key: 789


 38%|███▊      | 3/8 [00:38<01:02, 12.48s/it]

...

Key: 1876


 88%|████████▊ | 7/8 [01:05<00:07,  7.96s/it]

Key: 1989


100%|██████████| 8/8 [01:12<00:00,  9.05s/it]

Key: 2624


In [ ]:
stop here

In [9]:
df = pd.DataFrame(list(responses.items()), columns=["index", "response"])
df.to_parquet("novel_responses.parquet", index=False)